### Import libraries

In [2]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import matplotlib.cm as cm
import matplotlib.colors as colors

import folium


### Scrap data from Wikipedia page into a Pandas DataFrame

In [3]:
scrapdata = requests.get('https://en.wikipedia.org/wiki/Category:Suburbs_in_Kuala_Lumpur').text #gives the html code

In [4]:
soup = BeautifulSoup(scrapdata, 'lxml')

#print(soup.prettify())

In [26]:
#res = soup.find_all('div',class_ = 'mw-category')[0].find_all('li')
#res[0].text


'Alam Damai'

In [5]:
neighborhoods=[]

for row in soup.find_all('div',class_ = 'mw-category')[0].find_all('li'):
    neighborhoods.append(row.text)
    

In [6]:
kl_df=pd.DataFrame({'Neighborhood':neighborhoods})


In [7]:
kl_df.shape

(70, 1)

### Latitudes and Longitudes of the neighbourhood

In [8]:
Neighborhood_list =kl_df['Neighborhood'].to_list()


In [9]:
def get_lat_long(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Kuala Lumpur, Malaysia'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords


In [12]:
coordinates = []

for n in Neighborhood_list:
    coordinates.append(get_lat_long(n))

In [13]:
df_coords = pd.DataFrame(coordinates, columns = ['Latitude','Longitude'])


In [14]:
kl_df['Longitude']=df_coords['Longitude']
kl_df['Latitude']=df_coords['Latitude']


In [15]:
kl_df.shape


(70, 3)

### Visualizing the neighbours of KL

In [16]:
#get the coordinates of KL, Malaysia

address = 'Kuala Lumpur, Malaysia'

geolocator = Nominatim(user_agent = 'http')
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The Geographical coordinates of KL, Malaysia are {}, {}'.format(latitude,longitude))

The Geographical coordinates of KL, Malaysia are 3.1516964, 101.6942371


In [17]:
map_kl = folium.Map(location = [latitude, longitude], zoom_start= 11)


for lat,long,neighhood in zip(kl_df['Latitude'],kl_df['Longitude'], kl_df['Neighborhood']):
    label='{}'.format(neighhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_kl)  
    
    

map_kl.save('map_kl.html')

### Using Foursquare API to explore the neighbourhoods

In [18]:
# define Foursquare Credentials and Version
CLIENT_ID = 'TBWWVPK4I25HDQTFFBTO4VYED5WCZVWNT0RXCPWQSZZ5AEPY' # your Foursquare ID
CLIENT_SECRET = 'HARQN4PSOAZ0NJY4JSEDE0SKZK1ZJNCD005LNFNSHRDB01OG' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

#### Top 100 venues that are in a radius of 2000 metres

In [19]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(kl_df['Latitude'], kl_df['Longitude'], kl_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [20]:
venues_df =pd.DataFrame(venues)


In [21]:
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

In [22]:
venues_df

Neighborhood  Latitude   Longitude  \
0                       Alam Damai  3.057690  101.743880   
1                       Alam Damai  3.057690  101.743880   
2                       Alam Damai  3.057690  101.743880   
3                       Alam Damai  3.057690  101.743880   
4                       Alam Damai  3.057690  101.743880   
5                       Alam Damai  3.057690  101.743880   
6                       Alam Damai  3.057690  101.743880   
7                       Alam Damai  3.057690  101.743880   
8                       Alam Damai  3.057690  101.743880   
9                       Alam Damai  3.057690  101.743880   
10                      Alam Damai  3.057690  101.743880   
11                      Alam Damai  3.057690  101.743880   
12                      Alam Damai  3.057690  101.743880   
13                      Alam Damai  3.057690  101.743880   
14                      Alam Damai  3.057690  101.743880   
15                      Alam Damai  3.057690  101.743880   
16                      Alam Damai  3.057690  101.743880   
17                      Alam Damai  3.057690  101.743880   
18                      Alam Damai  3.057690  101.743880   
19                      Alam Damai  3.057690  101.743880   
20                      Alam Damai  3.057690  101.743880   
21                      Alam Damai  3.057690  101.743880   
22                      Alam Damai  3.057690  101.743880   
23                      Alam Damai  3.057690  101.743880   
24                      Alam Damai  3.057690  101.743880   
25                      Alam Damai  3.057690  101.743880   
26                      Alam Damai  3.057690  101.743880   
27                      Alam Damai  3.057690  101.743880   
28                      Alam Damai  3.057690  101.743880   
29                      Alam Damai  3.057690  101.743880   
30                      Alam Damai  3.057690  101.743880   
31                      Alam Damai  3.057690  101.743880   
32                      Alam Damai  3.057690  101.743880   
33                      Alam Damai  3.057690  101.743880   
34                      Alam Damai  3.057690  101.743880   
35                      Alam Damai  3.057690  101.743880   
36                      Alam Damai  3.057690  101.743880   
37                      Alam Damai  3.057690  101.743880   
38                      Alam Damai  3.057690  101.743880   
39                      Alam Damai  3.057690  101.743880   
40                      Alam Damai  3.057690  101.743880   
41                      Alam Damai  3.057690  101.743880   
42                      Alam Damai  3.057690  101.743880   
43                      Alam Damai  3.057690  101.743880   
44                      Alam Damai  3.057690  101.743880   
45                      Alam Damai  3.057690  101.743880   
46                      Alam Damai  3.057690  101.743880   
47                      Alam Damai  3.057690  101.743880   
48                      Alam Damai  3.057690  101.743880   
49                      Alam Damai  3.057690  101.743880   
50                      Alam Damai  3.057690  101.743880   
51                      Alam Damai  3.057690  101.743880   
52                      Alam Damai  3.057690  101.743880   
53                      Alam Damai  3.057690  101.743880   
54                      Alam Damai  3.057690  101.743880   
55                      Alam Damai  3.057690  101.743880   
56                      Alam Damai  3.057690  101.743880   
57                      Alam Damai  3.057690  101.743880   
58                      Alam Damai  3.057690  101.743880   
59                      Alam Damai  3.057690  101.743880   
60                      Alam Damai  3.057690  101.743880   
61                      Alam Damai  3.057690  101.743880   
62                      Alam Damai  3.057690  101.743880   
63                      Alam Damai  3.057690  101.743880   
64                      Alam Damai  3.057690  101.743880   
65                      Alam Damai  3.057690  101.743880   
66

In [23]:
venues_df.shape

(6993, 7)

In [24]:
venues_df.groupby(['Neighborhood']).count() #no of venues for each neighbourhood

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                                  
Alam Damai                         100        100        100            100   
Ampang, Kuala Lumpur               100        100        100            100   
Bandar Menjalara                   100        100        100            100   
Bandar Sri Permaisuri              100        100        100            100   
Bandar Tasik Selatan               100        100        100            100   
Bandar Tun Razak                   100        100        100            100   
Bangsar                            100        100        100            100   
Bangsar Park                       100        100        100            100   
Bangsar South                      100        100        100            100   
Batu 11 Cheras                     100        100        100            100   
Batu, Kuala Lumpur                 100        100        100            100   
Brickfields                        100        100        100            100   
Bukit Bintang                      100        100        100            100   
Bukit Jalil                        100        100        100            100   
Bukit Kiara                        100        100        100            100   
Bukit Nanas                        100        100        100            100   
Bukit Petaling                     100        100        100            100   
Bukit Tunku                        100        100        100            100   
Cheras, Kuala Lumpur               100        100        100            100   
Chow Kit                           100        100        100            100   
Damansara Heights                  100        100        100            100   
Damansara Town Centre              100        100        100            100   
Dang Wangi                         100        100        100            100   
Desa Petaling                      100        100        100            100   
Federal Hill, Kuala Lumpur         100        100        100            100   
Happy Garden                       100        100        100            100   
Jalan Cochrane, Kuala Lumpur       100        100        100            100   
Jinjang                            100        100        100            100   
KL Eco City                        100        100        100            100   
Kampung Baru, Kuala Lumpur         100        100        100            100   
Kampung Datuk Keramat              100        100        100            100   
Kampung Padang Balang               99         99         99             99   
Kepong                             100        100        100            100   
Kepong Baru                        100        100        100            100   
Kuchai Lama                        100        100        100            100   
Lembah Pantai                      100        100        100            100   
Maluri                             100        100        100            100   
Medan Tuanku                       100        100        100            100   
Miharja                            100        100        100            100   
Mont Kiara                         100        100        100            100   
Pantai Dalam                       100        100        100            100   
Pudu, Kuala Lumpur                 100        100        100            100   
Putrajaya                          100        100        100            100   
Salak South                        100        100        100            100   
Segambut                           100        100        100            100   
Semarak                            100        100        100            100   
Sentul, Kuala Lumpur               100        100        100            100   
Setapak                            100        100        100            100   
Setiawangsa                        100        100        100            100   
S

In [25]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique()))) #unique categories of venues

There are 308 uniques categories.


In [26]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:]

array(['Food & Drink Shop', 'Supplement Shop', 'Noodle House',
       'Breakfast Spot', 'Chinese Restaurant', 'Seafood Restaurant',
       'Restaurant', 'Food Court', 'Vegetarian / Vegan Restaurant',
       'Other Great Outdoors', 'Dim Sum Restaurant', 'Asian Restaurant',
       'Food Truck', 'Park', 'Indian Restaurant', 'Bubble Tea Shop',
       'Coffee Shop', 'Pet Store', 'Spa', 'Snack Place', 'Dessert Shop',
       'Chinese Breakfast Place', 'Outlet Store', 'Convenience Store',
       'Japanese Restaurant', 'Bakery', 'Malay Restaurant', 'Café',
       'Farmers Market', 'Mamak Restaurant', 'Cantonese Restaurant',
       'Athletics & Sports', 'Gym / Fitness Center', 'Steakhouse',
       'Fast Food Restaurant', 'Middle Eastern Restaurant',
       'Hakka Restaurant', 'Burger Joint', 'Badminton Court',
       'College Bookstore', 'Winery', 'Halal Restaurant', 'Grocery Store',
       'Shoe Store', 'Vietnamese Restaurant', 'Fish & Chips Shop',
       'Hostel', 'South Indian Restaurant', 'E

In [27]:
# check if the results contain "Shopping Mall"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

In [28]:
# one hot encoding
kl_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
kl_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [kl_onehot.columns[-1]] + list(kl_onehot.columns[:-1])
kl_onehot = kl_onehot[fixed_columns]

print(kl_onehot.shape)
kl_onehot.head()

(6993, 309)


Neighborhoods  Accessories Store  Adult Boutique  African Restaurant  \
0    Alam Damai                  0               0                   0   
1    Alam Damai                  0               0                   0   
2    Alam Damai                  0               0                   0   
3    Alam Damai                  0               0                   0   
4    Alam Damai                  0               0                   0   

   American Restaurant  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0                    0       0            0           0                    0   
1                    0       0            0           0                    0   
2                    0       0            0           0                    0   
3                    0       0            0           0                    0   
4                    0       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Auto Garage  \
0                 0                   0           0            0   
1                 0                   0           0            0   
2                 0                   0           0            0   
3                 0                   0           0            0   
4                 0                   0           0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Badminton Court  Bagel Shop  \
0              0                0          0                0           0   
1              0                0          0                0           0   
2              0                0          0                0           0   
3              0                0          0                0           0   
4              0                0          0                0           0   

   Bakery  Bar  Baseball Field  Basketball Court  Bed & Breakfast  Beer Bar  \
0       0    0               0                 0                0         0   
1       0    0               0                 0                0         0   
2       0    0               0                 0                0         0   
3       0    0               0                 0                0         0   
4       0    0               0                 0                0         0   

   Beer Garden  Bistro  Board Shop  Bookstore  Botanical Garden  Boutique  \
0            0       0           0          0                 0         0   
1            0       0           0          0                 0         0   
2            0       0           0          0                 0         0   
3            0       0           0          0                 0         0   
4            0       0           0          0                 0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     0               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0                     0               1        0   
4              0           0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0            0                0       0         0             0   
1            0                0       0         0             0   
2            0                0       0         0             0   
3            0                0       0         0             0   
4            0                0       0         0             0   

   Burrito Place  Business Service  Butcher  Café  Camera Store  Campground  \
0              0                 0        0     0             0           0   
1              0                 0        0     0             0           0   
2              0                 0        0     0             0           0   
3              0                 0        0     0             0         

In [30]:
kl_grouped = kl_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(kl_grouped.shape)
kl_grouped


(70, 309)


Neighborhoods   Zoo  Accessories Store  Adult Boutique  \
0                     Alam Damai  0.00               0.00            0.00   
1           Ampang, Kuala Lumpur  0.00               0.00            0.00   
2               Bandar Menjalara  0.00               0.00            0.00   
3          Bandar Sri Permaisuri  0.00               0.01            0.00   
4           Bandar Tasik Selatan  0.00               0.01            0.00   
5               Bandar Tun Razak  0.00               0.01            0.00   
6                        Bangsar  0.00               0.00            0.00   
7                   Bangsar Park  0.00               0.00            0.00   
8                  Bangsar South  0.00               0.00            0.00   
9                 Batu 11 Cheras  0.00               0.00            0.00   
10            Batu, Kuala Lumpur  0.00               0.00            0.01   
11                   Brickfields  0.00               0.00            0.00   
12                 Bukit Bintang  0.00               0.00            0.00   
13                   Bukit Jalil  0.00               0.00            0.00   
14                   Bukit Kiara  0.01               0.00            0.00   
15                   Bukit Nanas  0.00               0.00            0.00   
16                Bukit Petaling  0.00               0.01            0.00   
17                   Bukit Tunku  0.00               0.00            0.00   
18          Cheras, Kuala Lumpur  0.00               0.00            0.00   
19                      Chow Kit  0.00               0.00            0.01   
20             Damansara Heights  0.00               0.00            0.00   
21         Damansara Town Centre  0.00               0.00            0.00   
22                    Dang Wangi  0.00               0.00            0.00   
23                 Desa Petaling  0.00               0.01            0.00   
24    Federal Hill, Kuala Lumpur  0.00               0.00            0.00   
25                  Happy Garden  0.00               0.00            0.00   
26  Jalan Cochrane, Kuala Lumpur  0.00               0.00            0.00   
27                       Jinjang  0.00               0.01            0.00   
28                   KL Eco City  0.00               0.00            0.00   
29    Kampung Baru, Kuala Lumpur  0.00               0.01            0.00   
30         Kampung Datuk Keramat  0.00               0.00            0.00   
31         Kampung Padang Balang  0.00               0.00            0.00   
32                        Kepong  0.00               0.01            0.00   
33                   Kepong Baru  0.00               0.01            0.00   
34                   Kuchai Lama  0.00               0.00            0.00   
35                 Lembah Pantai  0.00               0.00            0.00   
36                        Maluri  0.00               0.00            0.01   
37                  Medan Tuanku  0.00               0.00            0.00   
38                       Miharja  0.00               0.00            0.01   
39                    Mont Kiara  0.00               0.00            0.00   
40                  Pantai Dalam  0.00               0.00            0.00   
41            Pudu, Kuala Lumpur  0.00               0.00            0.00   
42                     Putrajaya  0.00               0.00            0.00   
43                   Salak South  0.00               0.00            0.00   
44                      Segambut  0.00               0.00            0.00   
45                       Semarak  0.00               0.00            0.00   
46          Sentul, Kuala Lumpur  0.00               0.00            0.00   
47                       Setapak  0.00               0.00            0.00   
48                   Setiawangsa  0.00               0.00            0.00   
49                      Shamelin  0.00               0.00            0.00   
50                  Sri Hartamas  0.00               0.00            0.00   
51             

In [31]:
len(kl_grouped[kl_grouped["Shopping Mall"] > 0])

37

### Create a new DataFrame for Shopping Mall data only

In [33]:
kl_mall = kl_grouped[["Neighborhoods","Shopping Mall"]]

In [34]:
kl_mall.head()

Neighborhoods  Shopping Mall
0             Alam Damai           0.00
1   Ampang, Kuala Lumpur           0.01
2       Bandar Menjalara           0.01
3  Bandar Sri Permaisuri           0.00
4   Bandar Tasik Selatan           0.01

### Cluster neighborhoods

In [36]:
from sklearn.cluster import KMeans


# set number of clusters
kclusters = 3

kl_clustering = kl_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kl_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 0, 0, 2, 0, 2, 1, 1, 0, 2])

In [40]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
kl_merged = kl_mall.copy()

# add clustering labels
kl_merged["Cluster Labels"] = kmeans.labels_
kl_merged.head()

Neighborhoods  Shopping Mall  Cluster Labels
0             Alam Damai           0.00               2
1   Ampang, Kuala Lumpur           0.01               0
2       Bandar Menjalara           0.01               0
3  Bandar Sri Permaisuri           0.00               2
4   Bandar Tasik Selatan           0.01               0

In [41]:

kl_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
kl_merged.head()

Neighborhood  Shopping Mall  Cluster Labels
0             Alam Damai           0.00               2
1   Ampang, Kuala Lumpur           0.01               0
2       Bandar Menjalara           0.01               0
3  Bandar Sri Permaisuri           0.00               2
4   Bandar Tasik Selatan           0.01               0

In [42]:
kl_merged = kl_merged.join(kl_df.set_index("Neighborhood"), on="Neighborhood")

print(kl_merged.shape)
kl_merged.head() # check the last columns!

(70, 5)


Neighborhood  Shopping Mall  Cluster Labels   Longitude  Latitude
0             Alam Damai           0.00               2  101.743880  3.057690
1   Ampang, Kuala Lumpur           0.01               0  101.696728  3.148499
2       Bandar Menjalara           0.01               0  101.625450  3.190350
3  Bandar Sri Permaisuri           0.00               2  101.712260  3.103910
4   Bandar Tasik Selatan           0.01               0  101.714610  3.072750

In [43]:

# sort the results by Cluster Labels
print(kl_merged.shape)
kl_merged.sort_values(["Cluster Labels"], inplace=True)
kl_merged

(70, 5)


Neighborhood  Shopping Mall  Cluster Labels   Longitude  \
69                   Wangsa Maju       0.010000               0  101.737150   
21         Damansara Town Centre       0.010000               0  101.690294   
22                    Dang Wangi       0.020000               0  101.697280   
46          Sentul, Kuala Lumpur       0.010000               0  101.693050   
24    Federal Hill, Kuala Lumpur       0.010000               0  101.685640   
28                   KL Eco City       0.020000               0  101.673840   
30         Kampung Datuk Keramat       0.010000               0  101.730460   
56                    Taman Duta       0.020000               0  101.671840   
55                    Taman Desa       0.010000               0  101.684710   
68                    Titiwangsa       0.010000               0  101.703210   
37                  Medan Tuanku       0.020000               0  101.698340   
39                    Mont Kiara       0.020000               0  101.652430   
52                   Sungai Besi       0.010000               0  101.706030   
42                     Putrajaya       0.020000               0  101.718624   
44                      Segambut       0.020000               0  101.668100   
50                  Sri Hartamas       0.010000               0  101.650360   
20             Damansara Heights       0.020000               0  101.667950   
19                      Chow Kit       0.020000               0  101.698110   
49                      Shamelin       0.020000               0  101.735970   
17                   Bukit Tunku       0.020000               0  101.682760   
1           Ampang, Kuala Lumpur       0.010000               0  101.696728   
2               Bandar Menjalara       0.010000               0  101.625450   
4           Bandar Tasik Selatan       0.010000               0  101.714610   
12                 Bukit Bintang       0.020000               0  101.708550   
8                  Bangsar South       0.020000               0  101.662830   
16                Bukit Petaling       0.010000               0  101.698960   
15                   Bukit Nanas       0.020000               0  101.699854   
63               Taman Sri Sinar       0.010101               0  101.652930   
26  Jalan Cochrane, Kuala Lumpur       0.040000               1  101.721690   
11                   Brickfields       0.040000               1  101.684060   
29    Kampung Baru, Kuala Lumpur       0.030000               1  101.710280   
65           Taman Tun Dr Ismail       0.030000               1  101.622710   
7                   Bangsar Park       0.050000               1  101.678440   
35                 Lembah Pantai       0.040000               1  101.663889   
6                        Bangsar       0.050000               1  101.678440   
41            Pudu, Kuala Lumpur       0.040000               1  101.713070   
66                 Taman U-Thant       0.030000               1  101.724520   
59                  Taman Melati       0.000000               2  101.723990   
51                  Sri Petaling       0.000000               2  101.682520   
67                   Taman Wahyu       0.000000               2  101.671730   
54               Taman Connaught       0.000000               2  101.736890   
53            Taman Bukit Maluri       0.000000               2  101.633370   
61                     Taman OUG       0.000000               2  101.634508   
57                 Taman Ibukota       0.000000               2  101.715400   
64            Taman Taynton View       0.000000               2  101.736810   
58                Taman Len Seng       0.000000               2  101.742870   
62               Taman P. Ramlee       0.000000               2  101.705730   
60                   Taman Midah       0.000000               2  101.728370   
0                     Alam Damai       0.000000               2  101.743880   
47                       Setapak       0.000000               2  101.7

In [44]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kl_merged['Latitude'], kl_merged['Longitude'], kl_merged['Neighborhood'], kl_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [45]:
map_clusters.save('map_clusters.html')

In [46]:
kl_merged.loc[kl_merged['Cluster Labels'] == 0]

Neighborhood  Shopping Mall  Cluster Labels   Longitude  \
69                 Wangsa Maju       0.010000               0  101.737150   
21       Damansara Town Centre       0.010000               0  101.690294   
22                  Dang Wangi       0.020000               0  101.697280   
46        Sentul, Kuala Lumpur       0.010000               0  101.693050   
24  Federal Hill, Kuala Lumpur       0.010000               0  101.685640   
28                 KL Eco City       0.020000               0  101.673840   
30       Kampung Datuk Keramat       0.010000               0  101.730460   
56                  Taman Duta       0.020000               0  101.671840   
55                  Taman Desa       0.010000               0  101.684710   
68                  Titiwangsa       0.010000               0  101.703210   
37                Medan Tuanku       0.020000               0  101.698340   
39                  Mont Kiara       0.020000               0  101.652430   
52                 Sungai Besi       0.010000               0  101.706030   
42                   Putrajaya       0.020000               0  101.718624   
44                    Segambut       0.020000               0  101.668100   
50                Sri Hartamas       0.010000               0  101.650360   
20           Damansara Heights       0.020000               0  101.667950   
19                    Chow Kit       0.020000               0  101.698110   
49                    Shamelin       0.020000               0  101.735970   
17                 Bukit Tunku       0.020000               0  101.682760   
1         Ampang, Kuala Lumpur       0.010000               0  101.696728   
2             Bandar Menjalara       0.010000               0  101.625450   
4         Bandar Tasik Selatan       0.010000               0  101.714610   
12               Bukit Bintang       0.020000               0  101.708550   
8                Bangsar South       0.020000               0  101.662830   
16              Bukit Petaling       0.010000               0  101.698960   
15                 Bukit Nanas       0.020000               0  101.699854   
63             Taman Sri Sinar       0.010101               0  101.652930   

    Latitude  
69  3.203870  
21  3.136444  
22  3.157825  
46  3.175080  
24  3.136370  
28  3.117130  
30  3.166400  
56  3.155620  
55  3.102970  
68  3.180730  
37  3.159260  
39  3.165320  
52  3.049970  
42  3.125860  
44  3.186390  
50  3.162200  
20  3.147970  
19  3.163590  
49  3.124570  
17  3.173810  
1   3.148499  
2   3.190350  
4   3.072750  
12  3.147770  
8   3.111020  
16  3.129290  
15  3.148609  
63  3.190070

In [47]:
kl_merged.loc[kl_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  Cluster Labels   Longitude  \
26  Jalan Cochrane, Kuala Lumpur           0.04               1  101.721690   
11                   Brickfields           0.04               1  101.684060   
29    Kampung Baru, Kuala Lumpur           0.03               1  101.710280   
65           Taman Tun Dr Ismail           0.03               1  101.622710   
7                   Bangsar Park           0.05               1  101.678440   
35                 Lembah Pantai           0.04               1  101.663889   
6                        Bangsar           0.05               1  101.678440   
41            Pudu, Kuala Lumpur           0.04               1  101.713070   
66                 Taman U-Thant           0.03               1  101.724520   

    Latitude  
26  3.134630  
11  3.129160  
29  3.165460  
65  3.152830  
7   3.129200  
35  3.121189  
6   3.129200  
41  3.133540  
66  3.157700

In [48]:

kl_merged.loc[kl_merged['Cluster Labels'] == 2]

Neighborhood  Shopping Mall  Cluster Labels   Longitude  Latitude
59           Taman Melati            0.0               2  101.723990  3.223570
51           Sri Petaling            0.0               2  101.682520  3.072600
67            Taman Wahyu            0.0               2  101.671730  3.222400
54        Taman Connaught            0.0               2  101.736890  3.082690
53     Taman Bukit Maluri            0.0               2  101.633370  3.200660
61              Taman OUG            0.0               2  101.634508  3.210051
57          Taman Ibukota            0.0               2  101.715400  3.212160
64     Taman Taynton View            0.0               2  101.736810  3.087070
58         Taman Len Seng            0.0               2  101.742870  3.069080
62        Taman P. Ramlee            0.0               2  101.705730  3.193940
60            Taman Midah            0.0               2  101.728370  3.093590
0              Alam Damai            0.0               2  101.743880  3.057690
47                Setapak            0.0               2  101.704150  3.188160
3   Bandar Sri Permaisuri            0.0               2  101.712260  3.103910
5        Bandar Tun Razak            0.0               2  101.722810  3.082800
9          Batu 11 Cheras            0.0               2  101.746750  3.061870
10     Batu, Kuala Lumpur            0.0               2  101.694050  3.147890
13            Bukit Jalil            0.0               2  101.689650  3.057810
14            Bukit Kiara            0.0               2  101.644330  3.143480
18   Cheras, Kuala Lumpur            0.0               2  101.746750  3.061870
23          Desa Petaling            0.0               2  101.704380  3.083300
48            Setiawangsa            0.0               2  101.740066  3.191802
25           Happy Garden            0.0               2  101.721070  3.201630
31  Kampung Padang Balang            0.0               2  101.693180  3.209430
32                 Kepong            0.0               2  101.637630  3.217500
33            Kepong Baru            0.0               2  101.645173  3.207771
36                 Maluri            0.0               2  101.694050  3.147890
38                Miharja            0.0               2  101.694050  3.147890
40           Pantai Dalam            0.0               2  101.667470  3.094760
43            Salak South            0.0               2  101.696890  3.081540
45                Semarak            0.0               2  101.721449  3.179943
27                Jinjang            0.0               2  101.658740  3.209500
34            Kuchai Lama            0.0               2  101.677330  3.090740

Most of the shopping malls are concentrated in the central area of Kuala Lumpur city, with the highest numbers in cluster 1 and moderate numbers in cluster 0. Cluster 2 has almost no shopping malls in the neighborhoods. So, cluster 2 neighborhoods would be a great opportunity as there would be literally no competition with existing malls. Also, cluster 1 neighborhoods malls would likely be suffering from a lot of competition as there are a lot of malls.


Therefore,

 this project recommends property developers to open new shopping malls in neighborhoods in cluster 2 with little to no competition. 
 Property developers who have unique selling propositions and can stand out in the competition can open in the neighborhoods in cluster 0.
 Lastly, it would be an absolute NO to opening a new shopping mall in cluster 1 as there is already a lot of malls in the areas.